<a href="https://colab.research.google.com/github/zain910128/MS-Transport_Optimisation/blob/master/Transport_Optimisation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Open in Colab to view Maps and visualisations

Import packages and libraries

In [ ]:
import pandas as pd
import numpy as np
%config IPCompleter.greedy=True
!pip install geopandas
#!pip install geopy
import geopandas
import geopy
from geopy.geocoders import GoogleV3


In [ ]:
from sklearn.cluster import KMeans
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import MinMaxScaler
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline
import folium

In [ ]:
#load previously generated and saved adrs2 and stops2
adrs2= pd.read_csv("https://raw.githubusercontent.com/zain910128/MS-Transport_Optimisation/master/adrs2.csv")
stops2= pd.read_csv("https://raw.githubusercontent.com/zain910128/MS-Transport_Optimisation/master/stops2.csv")


#Skip to maps if running this cell

In [ ]:
stops = pd.read_csv("https://raw.githubusercontent.com/zain910128/MS-Transport_Optimisation/master/Bus_Stops.csv")
adrs = pd.read_csv("https://raw.githubusercontent.com/zain910128/MS-Transport_Optimisation/master/Employee_Addresses.csv")

In [ ]:
print(adrs.shape)
adrs.head()

(2191, 2)


address  employee_id
0   98 Edinburgh St, San Francisco, CA 94112, USA          206
1        237 Accacia St, Daly City, CA 94014, USA         2081
2    1835 Folsom St, San Francisco, CA 94103, USA          178
3  170 Cambridge St, San Francisco, CA 94134, USA           50
4     16 Roanoke St, San Francisco, CA 94131, USA         1863

In [ ]:
print(stops.shape)
stops.head()

(119, 2)


Street_One         Street_Two
0  MISSION ST          ITALY AVE
1  MISSION ST  NEW MONTGOMERY ST
2  MISSION ST            01ST ST
3  MISSION ST            20TH ST
4  MISSION ST         FREMONT ST

In [ ]:
#Split address in addresses dataframe to give Street address, City, Zip code, Country, employee id
adrs2 = adrs.copy()
adrs2[["Street","City","State_Zip","Country"]] = adrs2["address"].str.rsplit(pat=", ",expand= True, n=3)
adrs2[["State_code","Zip"]]=adrs2["State_Zip"].str.rsplit(pat=" ", expand=True, n=1)

#Correct an incorrect address spelling
adrs2.at[1582,"Street"] = "20 Marsily St"
adrs2.at[1582,"Street"]

'20 Marsily St'

In [ ]:
#Get lat-long for addresses
geolocator = GoogleV3(api_key="insert your key here")


In [ ]:
geocoded = []

for address in adrs2['address']:
  geocoded.append(geolocator.geocode(address, components={"country": "US"})) #Employee id 916 gives france address without country restriction


In [ ]:

latlong = pd.DataFrame()
latlong["raw"] = geocoded #geocoded is a Geo Series
latlong["lat_long"] = latlong['raw'].apply(lambda x: (x.latitude, x.longitude))
latlong["lat"] = latlong['raw'].apply(lambda x: (x.latitude))
latlong["long"] = latlong['raw'].apply(lambda x: (x.longitude))
latlong.shape

adrs2= pd.merge(adrs2,latlong,how="left", left_index=True, right_index=True)  #Running this line multiple times will create duplicate columns

adrs2.head()
#del(latlong)

In [ ]:
#Export split addresses for visualisation in Tableau
adrs2.to_csv("adrs2.csv", index=False)


In [ ]:
#adrs2 = adrs2.drop(columns=["address","State_Zip"])
adrs2.head()

address  ...        long
0   98 Edinburgh St, San Francisco, CA 94112, USA  ... -122.427326
1        237 Accacia St, Daly City, CA 94014, USA  ... -122.415878
2    1835 Folsom St, San Francisco, CA 94103, USA  ... -122.415181
3  170 Cambridge St, San Francisco, CA 94134, USA  ... -122.419661
4     16 Roanoke St, San Francisco, CA 94131, USA  ... -122.431322

[5 rows x 12 columns]

In [ ]:
adrs2[adrs2["Street"].astype(str).str.contains("NaN")]

Empty DataFrame
Columns: [address, employee_id, Street, City, State_Zip, Country, State_code, Zip, raw, lat_long, lat, long]
Index: []

In [ ]:
# Similarly Get lat-long of bus stops
stops2 = stops.copy()
stops2["Street_Two"]= stops2["Street_Two"].str.lstrip('0') 

stops2["intersection"] = stops2["Street_One"] + " & " + stops2["Street_Two"]
stops2['intersection'] = stops2['intersection'].str.replace('ST$',"Street, san francisco",regex=True)
stops2['intersection'] = stops2['intersection'].str.replace('AVE$',"Ave, san francisco",regex=True)


geocoded = []
for address in stops2['intersection']:
  geocoded.append(geolocator.geocode(address, components={"country": "US"}))
  
stops2['raw']= geocoded
stops2.head()

Street_One  ...                                                raw
0  MISSION ST  ...  (Mission St & Italy Ave, San Francisco, CA 941...
1  MISSION ST  ...  (Mission St & New Montgomery St, San Francisco...
2  MISSION ST  ...  (Mission St & 1st St, San Francisco, CA 94105,...
3  MISSION ST  ...  (Mission St & 20th St, San Francisco, CA 94110...
4  MISSION ST  ...  (Mission St & Fremont St, San Francisco, CA 94...

[5 rows x 4 columns]

In [ ]:
stops2[stops2['raw'].isna()]

Empty DataFrame
Columns: [Street_One, Street_Two, intersection, raw]
Index: []

In [ ]:
stops2.shape

(119, 6)

In [ ]:
stops2['lat'] = stops2['raw']
stops2['lat'] = stops2['lat'].apply(lambda x: x.latitude)

stops2['lat'] = stops2['raw'].apply(lambda x: x.latitude)
stops2['long'] = stops2['raw'].apply(lambda x: x.longitude)
print(stops2.shape)
stops2.head()

# May give AttributeError if non location (None) values received by geocoder. Run geocoder again and see if a particualr address is repeatedly being problematic.

(119, 6)


Street_One         Street_Two  ...        lat        long
0  MISSION ST          ITALY AVE  ...  37.718478 -122.439536
1  MISSION ST  NEW MONTGOMERY ST  ...  37.787456 -122.400523
2  MISSION ST             1ST ST  ...  37.789768 -122.397597
3  MISSION ST            20TH ST  ...  37.758640 -122.419077
4  MISSION ST         FREMONT ST  ...  37.790457 -122.396707

[5 rows x 6 columns]

In [ ]:
#Export split addresses for visualisation
stops2.to_csv("stops2.csv", index=False)


In [ ]:
geolocator.geocode("20 Marsily , San Francisco, CA 94112, USA", components={"country": "US"})

Location(20 Marsily, San Francisco, CA 94112, USA, (37.7339389, -122.4279452, 0.0))

## Visualising addresses on a map for ease of understanding

In [ ]:
data_map = folium.Map(prefer_canvas=True)

def plotDot(point, color, label):
    '''input: series that contains a numeric named latitude and a numeric named longitude
    this function creates a CircleMarker and adds it to your this_map'''
    folium.CircleMarker(location=[point.lat, point.long],
                        radius=2, color = color,
                        weight=2, popup=point[label]).add_to(data_map)
    
#use df.apply(,axis=1) to "iterate" through every row in your dataframe
stops2.apply(plotDot, color="#007849", label="Street_Two", axis = 1)
adrs2.apply(plotDot, color="blue", label="Street", axis = 1)

#Set the zoom to the maximum possible
data_map.fit_bounds(data_map.get_bounds())

#Save the map to an HTML file
data_map.save('simple_dot_plot.html')

data_map

In the above map, 

Blue = Employee addresses

Green = Potential Bus Stops

In [ ]:
adrs2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2191 entries, 0 to 2190
Data columns (total 8 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   address      2191 non-null   object
 1   employee_id  2191 non-null   int64 
 2   Street       2191 non-null   object
 3   City         2191 non-null   object
 4   State_Zip    2191 non-null   object
 5   Country      2191 non-null   object
 6   State_code   2191 non-null   object
 7   Zip          2190 non-null   object
dtypes: int64(1), object(7)
memory usage: 137.1+ KB


In [ ]:
adrs3 = adrs2[['lat','long']].copy()

In [ ]:
adrs3.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2191 entries, 0 to 2190
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   lat     2191 non-null   float64
 1   long    2191 non-null   float64
dtypes: float64(2)
memory usage: 34.4 KB


## K Means Clustering

In [ ]:
X = np.array(adrs3.astype(float))
X

array([[  37.7274747, -122.4273257],
       [  37.7042048, -122.4158777],
       [  37.7679315, -122.4151808],
       ...,
       [  37.730796 , -122.41718  ],
       [  37.7123188, -122.4296911],
       [  37.762178 , -122.4140546]])

In [ ]:
kmeans = KMeans(n_clusters=10)
kmeans.fit(X)

KMeans(algorithm='auto', copy_x=True, init='k-means++', max_iter=300,
       n_clusters=10, n_init=10, n_jobs=None, precompute_distances='auto',
       random_state=None, tol=0.0001, verbose=0)

In [ ]:
X

array([[  37.7274747, -122.4273257],
       [  37.7042048, -122.4158777],
       [  37.7679315, -122.4151808],
       ...,
       [  37.730796 , -122.41718  ],
       [  37.7123188, -122.4296911],
       [  37.762178 , -122.4140546]])

In [ ]:
centroids = kmeans.cluster_centers_
centroids

array([[  37.76798878, -122.43002465],
       [  37.71206169, -122.44174474],
       [  37.73823451, -122.4282753 ],
       [  37.76994792, -122.41334561],
       [  37.79250558, -122.44355597],
       [  37.70982593, -122.41263279],
       [  37.73515332, -122.40263457],
       [  37.72660183, -122.42653009],
       [  37.74376499, -122.44878199],
       [  37.78496737, -122.39674017]])

In [ ]:
centroids = pd.DataFrame({'lat':centroids[:, 0],'long':centroids[:, 1] })
centroids

lat        long
0  37.767989 -122.430025
1  37.712062 -122.441745
2  37.738235 -122.428275
3  37.769948 -122.413346
4  37.792506 -122.443556
5  37.709826 -122.412633
6  37.735153 -122.402635
7  37.726602 -122.426530
8  37.743765 -122.448782
9  37.784967 -122.396740

In [ ]:
# Find stops nearest to each centroid

from geopy.distance import geodesic

coid_stop = pd.DataFrame(columns=['lat','long'])
stops3 = stops2[['lat','long']].copy()

for index, point in centroids.iterrows():
  coidindex = index
  dist = 100
  for index, stop in stops3.iterrows():
    if dist > geodesic((stop.lat,stop.long),(point.lat,point.long)).km:
      dist = geodesic((stop.lat,stop.long),(point.lat,point.long)).km
      stopindex = index   
      
  coid_stop.at[coidindex,'lat'] = stops3.at[stopindex,'lat']
  coid_stop.at[coidindex,'long'] = stops3.at[stopindex,'long']

coid_stop


lat     long
0  37.7683  -122.42
1  37.7134 -122.444
2  37.7388 -122.424
3   37.771  -122.42
4  37.7731 -122.419
5  37.7216 -122.437
6  37.7428 -122.422
7  37.7292 -122.431
8  37.7309 -122.429
9  37.7875 -122.401

In [ ]:
data_map = folium.Map(prefer_canvas=True, tiles= "Stamen Toner")

def plotDot(point, color, label, radius, weight):
    '''input: series that contains a numeric named latitude and a numeric named longitude
    this function creates a CircleMarker and adds it to your this_map'''
    folium.CircleMarker(location=[point.lat, point.long],
                        radius=radius, color = color, 
                        popup=str(point[label]) if label in point else (None if label == 'None' else label),
                        weight=weight).add_to(data_map)
    
#use df.apply(,axis=1) to "iterate" through every row in your dataframe
stops2.apply(plotDot, color="#aed581", label="Street_Two", radius=3, weight=3.8, axis = 1)
adrs2.apply(plotDot, color="#8e24aa",label="employee_id", radius=3, weight=5, axis = 1)
centroids.apply(plotDot, color="#0097a7",label="Group Centroid", radius=3, weight=5, axis = 1)
coid_stop.apply(plotDot, color="#ff4081", label = "None", radius=6, weight=2, axis = 1)                        

#Set the zoom to the maximum possible
data_map.fit_bounds(data_map.get_bounds())

#Save the map to an HTML file
data_map.save('simple_dot_plot.html')

data_map

In the above map:

- Magenta = Employee address. On click, you can see the employee numbers
- Light green = Potential bus stops. On click, you can see the intersection name.
- Dark Green = Centroid of each cluster.
- Pink Border = The bus stop nearest to each centroid. You can click inside the border to see the name of the intersection.
